In [11]:
import pandas as pd
import pickle
from statsmodels.tsa.api import ExponentialSmoothing
import plotly.express as px


In [12]:
# URLs for training and test datasets
train_data_url = "https://github.com/dustywhite7/econ8310-assignment1/raw/main/assignment_data_train.csv"

# Load the training data
train_df = pd.read_csv(train_data_url, parse_dates=['Timestamp'], index_col='Timestamp')

# Ensure the index is properly formatted as datetime
train_df.index = train_df.index.to_period("h").to_timestamp()

# Visualize the data
px.line(train_df, x=train_df.index, y='trips', title='NYC Taxi Trips Over Time', labels={'x': 'Timestamp', 'trips': 'Number of Trips'})


In [13]:
from statsmodels.tsa.api import SimpleExpSmoothing
import plotly.graph_objects as go

# Extract the 'trips' column as the time series
trips = train_df['trips']

# Define smoothing levels and fit the models
alpha020 = SimpleExpSmoothing(trips).fit(smoothing_level=0.2, optimized=False)
alpha050 = SimpleExpSmoothing(trips).fit(smoothing_level=0.5, optimized=False)
alpha080 = SimpleExpSmoothing(trips).fit(smoothing_level=0.8, optimized=False)

# Forecast for the next 10 hours
forecast020 = alpha020.forecast(10)
forecast050 = alpha050.forecast(10)
forecast080 = alpha080.forecast(10)

# Create a DataFrame for the smoothed values
smoothData = pd.DataFrame({
    'Truth': trips.values,
    'alpha=0.2': alpha020.fittedvalues.values,
    'alpha=0.5': alpha050.fittedvalues.values,
    'alpha=0.8': alpha080.fittedvalues.values
}, index=trips.index)

# Plot the original data and smoothed values
fig = px.line(
    smoothData, 
    y=['Truth', 'alpha=0.2', 'alpha=0.5', 'alpha=0.8'], 
    x=smoothData.index,
    title="Simple Exponential Smoothing with Different Alphas",
    labels={"x": "Timestamp", "value": "Number of Trips"},
    color_discrete_map={
        "Truth": 'blue',
        'alpha=0.2': 'red', 
        'alpha=0.5': 'green', 
        'alpha=0.8': 'purple'
    }
)

# Add forecasts to the plot
fig.add_trace(go.Scatter(x=forecast020.index, y=forecast020.values, name='Forecast alpha=0.2', line={'color': 'red'}))
fig.add_trace(go.Scatter(x=forecast050.index, y=forecast050.values, name='Forecast alpha=0.5', line={'color': 'green'}))
fig.add_trace(go.Scatter(x=forecast080.index, y=forecast080.values, name='Forecast alpha=0.8', line={'color': 'purple'}))

# Display the plot
fig.show()


In [14]:
from statsmodels.tsa.api import SimpleExpSmoothing
import plotly.graph_objects as go

# Fit the Simple Exponential Smoothing model with optimized alpha
alphaBest = SimpleExpSmoothing(trips).fit()

# Forecast for the next 10 hours
forecast = alphaBest.forecast(10)

# Create a DataFrame for the smoothed values
smoothData = pd.DataFrame({
    'Truth': trips.values,
    'Best Fit Model': alphaBest.fittedvalues.values
}, index=trips.index)

# Plot the original data and the smoothed best-fit model
fig = px.line(
    smoothData,
    y=['Truth', 'Best Fit Model'],
    x=smoothData.index,
    title="Simple Exponential Smoothing with Optimized Alpha",
    labels={"x": "Timestamp", "value": "Number of Trips"},
    color_discrete_map={
        "Truth": 'blue',
        'Best Fit Model': 'red'
    }
)

# Update x-axis to show the range of interest (last 50 points + forecast range)
fig.update_xaxes(range=[smoothData.index[-50], forecast.index[-1]])

# Add the forecast to the plot
fig.add_trace(
    go.Scatter(
        x=forecast.index,
        y=forecast.values,
        name='Forecast',
        line={'color': 'red', 'dash': 'dash'}
    )
)

# Display the plot
fig.show()


C:\Users\ashaik\AppData\Local\Adobe\anaconda33\Lib\site-packages\statsmodels\tsa\holtwinters\model.py:918: ConvergenceWarning:

Optimization failed to converge. Check mle_retvals.



In [16]:
# Fit the Exponential Smoothing model with a linear trend
trend = ExponentialSmoothing(trips, trend='add', seasonal=None, damped=False).fit()

# Fit the Exponential Smoothing model with a damped linear trend
dampedTrend = ExponentialSmoothing(trips, trend='add', seasonal=None, damped=True, use_boxcox=True).fit()

# Forecast for the next 10 hours for both models
forecast_t = trend.forecast(10)
forecast_dt = dampedTrend.forecast(10)

# Create a DataFrame to store the Truth, Trend, and Damped Trend values
smoothData = pd.DataFrame({
    'Truth': trips.values,
    'Trend': trend.fittedvalues.values,
    'Damped Trend': dampedTrend.fittedvalues.values
}, index=trips.index)

# Plot the data
fig = px.line(
    smoothData,
    y=['Truth', 'Trend', 'Damped Trend'],
    x=smoothData.index,
    title="Linear and Damped Trends",
    labels={"x": "Timestamp", "value": "Number of Trips"},
    color_discrete_map={
        "Truth": 'blue',
        'Trend': 'red',
        'Damped Trend': 'green'
    }
)

# Update x-axis to focus on the last 50 points and include the forecast range
fig.update_xaxes(range=[smoothData.index[-50], forecast_t.index[-1]])

# Add the forecast lines to the plot
fig.add_trace(
    go.Scatter(
        x=forecast_t.index,
        y=forecast_t.values,
        name='Forecast Trend',
        line={'color': 'red', 'dash': 'dash'}
    )
)
fig.add_trace(
    go.Scatter(
        x=forecast_dt.index,
        y=forecast_dt.values,
        name='Forecast Damped Trend',
        line={'color': 'green', 'dash': 'dash'}
    )
)

# Show the plot
fig.show()


<positron-console-cell-16>:2: FutureWarning:

the 'damped' keyword is deprecated, use 'damped_trend' instead.

C:\Users\ashaik\AppData\Local\Adobe\anaconda33\Lib\site-packages\statsmodels\tsa\holtwinters\model.py:918: ConvergenceWarning:

Optimization failed to converge. Check mle_retvals.

<positron-console-cell-16>:5: FutureWarning:

the 'damped' keyword is deprecated, use 'damped_trend' instead.

C:\Users\ashaik\AppData\Local\Adobe\anaconda33\Lib\site-packages\statsmodels\tsa\holtwinters\model.py:918: ConvergenceWarning:

Optimization failed to converge. Check mle_retvals.



In [17]:
from statsmodels.tsa.api import ExponentialSmoothing
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go

# Assuming 'trips' is the time series we are working with
# trips = train_df['trips']

# Fit the Exponential Smoothing model with additive trend and seasonality
trend_seasonal = ExponentialSmoothing(trips, trend='add', seasonal='add', seasonal_periods=24).fit()

# Fit the Exponential Smoothing model with damped multiplicative trend and additive seasonality
damped_trend_seasonal = ExponentialSmoothing(trips, trend='mul', seasonal='add', damped=True, seasonal_periods=24).fit()

# Forecast for the next 10 hours for both models
forecast_ts = trend_seasonal.forecast(10)
forecast_dts = damped_trend_seasonal.forecast(10)

# Create a DataFrame for the fitted values
smoothData = pd.DataFrame({
    'Truth': trips.values,
    'Trend + Seasonal': trend_seasonal.fittedvalues.values,
    'Damped Trend + Seasonal': damped_trend_seasonal.fittedvalues.values
}, index=trips.index)

# Plotting the original data and fitted models
fig = px.line(
    smoothData,
    y=['Truth', 'Trend + Seasonal', 'Damped Trend + Seasonal'],
    x=smoothData.index,
    title='Linear and Damped Trends with Seasonality',
    labels={"x": "Timestamp", "value": "Number of Trips"},
    color_discrete_map={
        "Truth": 'blue',
        'Trend + Seasonal': 'red',
        'Damped Trend + Seasonal': 'green'
    }
)

# Update x-axis to focus on the last 50 points and include forecast range
fig.update_xaxes(range=[smoothData.index[-50], forecast_ts.index[-1]])

# Adding the forecast lines to the plot
fig.add_trace(
    go.Scatter(
        x=forecast_ts.index,
        y=forecast_ts.values,
        name='Forecast Trend + Seasonal',
        line={'color': 'red', 'dash': 'dash'}
    )
)
fig.add_trace(
    go.Scatter(
        x=forecast_dts.index,
        y=forecast_dts.values,
        name='Forecast Damped Trend + Seasonal',
        line={'color': 'green', 'dash': 'dash'}
    )
)

# Show the plot
fig.show()


C:\Users\ashaik\AppData\Local\Adobe\anaconda33\Lib\site-packages\statsmodels\tsa\holtwinters\model.py:918: ConvergenceWarning:

Optimization failed to converge. Check mle_retvals.

<positron-console-cell-17>:13: FutureWarning:

the 'damped' keyword is deprecated, use 'damped_trend' instead.

C:\Users\ashaik\AppData\Local\Adobe\anaconda33\Lib\site-packages\statsmodels\tsa\holtwinters\model.py:918: ConvergenceWarning:

Optimization failed to converge. Check mle_retvals.

